In [1]:
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

Mon Apr 14 06:12:55 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 570.124.06             Driver Version: 570.124.06     CUDA Version: 12.8     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA A100 80GB PCIe          Off |   00000001:00:00.0 Off |                    0 |
| N/A   33C    P0             64W /  300W |       1MiB /  81920MiB |      1%      Default |
|                                         |                        |             Disabled |
+-----------------------------------------+-----

In [4]:
!sudo add-apt-repository -y ppa:jonathonf/ffmpeg-4
!sudo apt update
!sudo apt install -y ffmpeg
!pip install datasets>=2.6.1
!pip install git+https://github.com/huggingface/transformers
!pip install librosa
!pip install evaluate>=0.30
!pip install jiwer
!pip install gradio
!pip install -q bitsandbytes datasets accelerate loralib
!pip install -q git+https://github.com/huggingface/transformers.git@main git+https://github.com/huggingface/peft.git@main

Repository: 'Types: deb
URIs: https://ppa.launchpadcontent.net/jonathonf/ffmpeg-4/ubuntu/
Suites: noble
Components: main
'
Description:
Backport of FFmpeg 4 and associated libraries. Now includes AOM/AV1 support!

FDK AAC is not compatible with GPL and FFmpeg can't be redistributed with it included. Please don't ask for it to be added to this public PPA.

---

PPA supporters:

BigBlueButton (https://bigbluebutton.org)

---

Donate to FFMPEG: https://ffmpeg.org/donations.html
Donate to Debian: https://www.debian.org/donations
Donate to this PPA: https://ko-fi.com/jonathonf
More info: https://launchpad.net/~jonathonf/+archive/ubuntu/ffmpeg-4
Adding repository.
Found existing deb entry in /etc/apt/sources.list.d/jonathonf-ubuntu-ffmpeg-4-noble.sources
Hit:1 http://azure.archive.ubuntu.com/ubuntu noble InRelease
Get:2 http://azure.archive.ubuntu.com/ubuntu noble-updates InRelease [126 kB]
Hit:3 http://azure.archive.ubuntu.com/ubuntu noble-backports InRelease         
Get:4 http://azure.arc

In [2]:
import os
import torch
import evaluate
import logging
from dataclasses import dataclass
from typing import Any, Dict, List, Union

from datasets import load_dataset, DatasetDict, Audio
from transformers import (
    WhisperFeatureExtractor,
    WhisperTokenizer,
    WhisperProcessor,
    WhisperForConditionalGeneration,
    Seq2SeqTrainingArguments,
    Seq2SeqTrainer,
    BitsAndBytesConfig,
    AutomaticSpeechRecognitionPipeline,
)
from peft import (
    prepare_model_for_kbit_training,
    LoraConfig,
    PeftModel,
    LoraModel,
    get_peft_model,
    PeftConfig,
    TaskType
)
from huggingface_hub import notebook_login, upload_folder
import gradio as gr

# --- Configuration ---
MODEL_NAME_OR_PATH = "openai/whisper-large-v2" 
LANGUAGE = "Uzbek"
LANGUAGE_ABBR = "uz"
TASK = "transcribe"
DATASET_NAME = "mozilla-foundation/common_voice_17_0"

OUTPUT_DIR = "./whisper-uzbek-results"
MODEL_SAVE_PATH = "./uzbek-stt" 
REPO_NAME = "ibodullo2205/uzbek-stt" 



In [ ]:
from huggingface_hub import login

login()


from datasets import load_dataset, DatasetDict

common_voice = DatasetDict()

# Load the dataset with `trust_remote_code=True`
common_voice["train"] = load_dataset(
    "mozilla-foundation/common_voice_17_0", "uz", split="train", trust_remote_code=True
)
common_voice["test"] = load_dataset(
    "mozilla-foundation/common_voice_17_0", "uz", split="test", trust_remote_code=True
)

print(common_voice)

DatasetDict({
    train: Dataset({
        features: ['client_id', 'path', 'audio', 'sentence', 'up_votes', 'down_votes', 'age', 'gender', 'accent', 'locale', 'segment', 'variant'],
        num_rows: 48475
    })
    test: Dataset({
        features: ['client_id', 'path', 'audio', 'sentence', 'up_votes', 'down_votes', 'age', 'gender', 'accent', 'locale', 'segment', 'variant'],
        num_rows: 12348
    })
})


In [18]:
common_voice = common_voice.remove_columns(["accent", "age", "client_id", "down_votes", "gender", "locale", "path", "segment", "up_votes", "variant"])

In [19]:
common_voice

DatasetDict({
    train: Dataset({
        features: ['audio', 'sentence'],
        num_rows: 48475
    })
    test: Dataset({
        features: ['audio', 'sentence'],
        num_rows: 12348
    })
})

In [20]:
common_voice["train"] = common_voice["train"].shuffle(seed=42)
common_voice["test"] = common_voice["test"].shuffle(seed=42)

In [3]:
# Load the feature extractor
feature_extractor = WhisperFeatureExtractor.from_pretrained("openai/whisper-large-v2")
# Load the tokenizer
tokenizer = WhisperTokenizer.from_pretrained("openai/whisper-large-v2")
# Load the processor
processor = WhisperProcessor.from_pretrained("openai/whisper-large-v2", language=LANGUAGE_ABBR, task=TASK)
 


print(feature_extractor)
print(tokenizer)
print(processor)

WhisperFeatureExtractor {
  "chunk_length": 30,
  "dither": 0.0,
  "feature_extractor_type": "WhisperFeatureExtractor",
  "feature_size": 80,
  "hop_length": 160,
  "n_fft": 400,
  "n_samples": 480000,
  "nb_max_frames": 3000,
  "padding_side": "right",
  "padding_value": 0.0,
  "processor_class": "WhisperProcessor",
  "return_attention_mask": false,
  "sampling_rate": 16000
}

WhisperTokenizer(name_or_path='openai/whisper-large-v2', vocab_size=50258, model_max_length=1024, is_fast=False, padding_side='right', truncation_side='right', special_tokens={'bos_token': '<|endoftext|>', 'eos_token': '<|endoftext|>', 'unk_token': '<|endoftext|>', 'pad_token': '<|endoftext|>', 'additional_special_tokens': ['<|endoftext|>', '<|startoftranscript|>', '<|en|>', '<|zh|>', '<|de|>', '<|es|>', '<|ru|>', '<|ko|>', '<|fr|>', '<|ja|>', '<|pt|>', '<|tr|>', '<|pl|>', '<|ca|>', '<|nl|>', '<|ar|>', '<|sv|>', '<|it|>', '<|id|>', '<|hi|>', '<|fi|>', '<|vi|>', '<|he|>', '<|uk|>', '<|el|>', '<|ms|>', '<|cs|>', '

In [4]:
print(common_voice["train"][0])

NameError: name 'common_voice' is not defined

In [23]:
common_voice = common_voice.cast_column("audio", Audio(sampling_rate=16000))

In [24]:
print(common_voice["train"][0])

{'audio': {'path': '/home/azureuser/.cache/huggingface/datasets/downloads/extracted/00152a35f134dccc1cbc3a5f6d4a8d49f1a2fb3413d65dc0ee24322235420755/uz_train_0/common_voice_uz_30011356.mp3', 'array': array([ 1.81898940e-12,  0.00000000e+00,  3.27418093e-11, ...,
       -5.76364982e-08,  8.70677468e-08, -1.91248546e-08]), 'sampling_rate': 16000}, 'sentence': 'Afsuski, bir nechta yaxshi istisnolardan tashqari, takliflarning aksariyati yomon va sifatsiz'}


In [25]:
def prepare_dataset(batch):
    # load and resample audio data from 48 to 16kHz
    audio = batch["audio"]

    # compute log-Mel input features from input audio array
    batch["input_features"] = feature_extractor(audio["array"], sampling_rate=audio["sampling_rate"]).input_features[0]

    # encode target text to label ids
    batch["labels"] = tokenizer(batch["sentence"]).input_ids
    return batch

In [26]:
print(common_voice)

DatasetDict({
    train: Dataset({
        features: ['audio', 'sentence'],
        num_rows: 48475
    })
    test: Dataset({
        features: ['audio', 'sentence'],
        num_rows: 12348
    })
})


In [27]:
print(common_voice.column_names["train"])

['audio', 'sentence']


In [28]:
common_voice = common_voice.map(prepare_dataset, remove_columns=common_voice.column_names["train"], num_proc=4)

Map (num_proc=4):   0%|          | 0/48475 [00:00<?, ? examples/s]

Map (num_proc=4):   0%|          | 0/12348 [00:00<?, ? examples/s]

In [5]:
# common_voice.save_to_disk("common_voice_uzbek")
common_voice = DatasetDict.load_from_disk("common_voice_uzbek")
print(common_voice)
print(common_voice["train"][0])

Loading dataset from disk:   0%|          | 0/94 [00:00<?, ?it/s]

Loading dataset from disk:   0%|          | 0/24 [00:00<?, ?it/s]

DatasetDict({
    train: Dataset({
        features: ['input_features', 'labels'],
        num_rows: 48475
    })
    test: Dataset({
        features: ['input_features', 'labels'],
        num_rows: 12348
    })
})
{'input_features': [[-0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295809745788574, -0.6295

In [6]:
import torch
from dataclasses import dataclass
from typing import Any, Dict, List, Union

@dataclass
class DataCollatorSpeechSeq2SeqWithPadding:
    processor: Any
    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lengths and need different padding methods
        # first treat the audio inputs by simply returning torch tensors
        input_features = [{"input_features": feature["input_features"]} for feature in features]
        batch = self.processor.feature_extractor.pad(input_features, return_tensors="pt")
        # get the tokenized label sequences
        label_features = [{"input_ids": feature["labels"]} for feature in features]
        # pad the labels to max length
        labels_batch = self.processor.tokenizer.pad(label_features, return_tensors="pt")
        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)
        # if bos token is appended in previous tokenization step,
        # cut bos token here as it's append later anyways
        if (labels[:, 0] == self.processor.tokenizer.bos_token_id).all().cpu().item():
            labels = labels[:, 1:]
        batch["labels"] = labels
        return batch

In [7]:
data_collator = DataCollatorSpeechSeq2SeqWithPadding(processor=processor)

In [8]:
import evaluate

metric = evaluate.load("wer")

In [9]:
def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids
    # replace -100 with the pad_token_id
    label_ids[label_ids == -100] = tokenizer.pad_token_id
    # we do not want to group tokens when computing the metrics
    pred_str = tokenizer.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = tokenizer.batch_decode(label_ids, skip_special_tokens=True)
    wer = 100 * metric.compute(predictions=pred_str, references=label_str)
    return {"wer": wer}

In [10]:
from transformers import WhisperForConditionalGeneration

model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-large-v2", load_in_8bit=True, device_map="auto")

The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.


In [11]:
model.generation_config.language = "uzbek"
model.generation_config.task = "transcribe"

model.generation_config.forced_decoder_ids = None

In [12]:
from peft import LoraConfig, get_peft_model

# Define LoRA configuration
config = LoraConfig(
    r=32,              # Rank of the low-rank adaptation
    lora_alpha=64,     # Scaling factor
    target_modules=["q_proj", "v_proj"],  # Modules to apply LoRA to
    lora_dropout=0.05, # Dropout rate for LoRA layers
    bias="none"
)

# Apply LoRA to the model
model = get_peft_model(model, config)

# Print trainable parameters to verify
model.print_trainable_parameters()

trainable params: 15,728,640 || all params: 1,559,033,600 || trainable%: 1.0089


In [13]:
!wandb login

wandb: Currently logged in as: ioa22052005 (ioa22052005-individual) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


In [14]:
if hasattr(model, "enable_input_require_grads"):
    model.enable_input_require_grads()
else:
    def make_inputs_require_grad(module, input, output):
         output.requires_grad_(True)

    model.get_input_embeddings().register_forward_hook(make_inputs_require_grad)

In [28]:
from transformers import Seq2SeqTrainingArguments

training_args = Seq2SeqTrainingArguments(
    output_dir="./whisper-uz-adv",
    per_device_train_batch_size=16,  
    gradient_accumulation_steps=1,  
    learning_rate=1e-5,
    warmup_steps=500,
    max_steps=2000,
    gradient_checkpointing=True,
    fp16=True,
    eval_strategy="steps",
    per_device_eval_batch_size=16,
    predict_with_generate=True,
    generation_max_length=225,
    save_steps=1000,
    eval_steps=500,
    logging_steps=25,
    label_names=["labels"],
    report_to=["wandb", "tensorboard"],
    load_best_model_at_end=True,
    metric_for_best_model="eval_loss",
    greater_is_better=False,
    push_to_hub=True,
)

In [29]:
from transformers import Seq2SeqTrainer

trainer = Seq2SeqTrainer(
    args=training_args,
    model=model,
    train_dataset=common_voice["train"],
    eval_dataset=common_voice["test"],
    data_collator=data_collator,
    tokenizer=processor,
)
model.config.use_cache = False 

/tmp/ipykernel_24447/170690088.py:3: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Seq2SeqTrainer.__init__`. Use `processing_class` instead.
  trainer = Seq2SeqTrainer(


In [23]:
torch.cuda.empty_cache()

In [30]:
processor.save_pretrained(training_args.output_dir)

[]

In [36]:
kwargs = {
    "dataset_tags": "mozilla-foundation/common_voice_17_0",
    "dataset": "Common Voice 17.0",
    "dataset_args": "config: uz, split: test",
    "language": "uz",
    "model_name": "Uzbek STT",
    "license": "mit",
    "finetuned_from": "openai/whisper-large-v2",
    "tasks": "automatic-speech-recognition",
}

In [32]:
trainer.train()

/home/azureuser/ibodullo/env/lib/python3.12/site-packages/torch/utils/checkpoint.py:87: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn(
/home/azureuser/ibodullo/env/lib/python3.12/site-packages/bitsandbytes/autograd/_functions.py:315: UserWarning: MatMul8bitLt: inputs will be cast from torch.float32 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during quantization")


NaN or Inf found in input tensor.
/home/azureuser/ibodullo/env/lib/python3.12/site-packages/torch/utils/checkpoint.py:87: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn(
/home/azureuser/ibodullo/env/lib/python3.12/site-packages/bitsandbytes/autograd/_functions.py:315: UserWarning: MatMul8bitLt: inputs will be cast from torch.float32 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during quantization")


TrainOutput(global_step=2000, training_loss=1.990606372833252, metrics={'train_runtime': 12416.4966, 'train_samples_per_second': 2.577, 'train_steps_per_second': 0.161, 'total_flos': 6.86662483968e+19, 'train_loss': 1.990606372833252, 'epoch': 0.6600660066006601})

In [37]:
trainer.push_to_hub(**kwargs)

events.out.tfevents.1744689547.interns:   0%|          | 0.00/25.5k [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/mustafoyev202/whisper-uz-adv/commit/a7e7cb3219a35bebb5656dc7eafb1a744e3897dd', commit_message='End of training', commit_description='', oid='a7e7cb3219a35bebb5656dc7eafb1a744e3897dd', pr_url=None, repo_url=RepoUrl('https://huggingface.co/mustafoyev202/whisper-uz-adv', endpoint='https://huggingface.co', repo_type='model', repo_id='mustafoyev202/whisper-uz-adv'), pr_revision=None, pr_num=None)

In [39]:
# Load model directly
model = WhisperForConditionalGeneration.from_pretrained(training_args.output_dir, device_map="auto", load_in_8bit=True)
preprocessor = WhisperProcessor.from_pretrained(training_args.output_dir, language=LANGUAGE_ABBR, task=TASK)

The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.


In [40]:
from transformers import pipeline
import gradio as gr

pipe = pipeline(
    task="automatic-speech-recognition", 
    model=model, 
    tokenizer=processor.tokenizer, 
    feature_extractor=processor.feature_extractor, 
    return_timestamps=True 
)

def transcribe(audio):
    text = pipe(audio)["text"]
    return text

iface = gr.Interface(
    fn=transcribe,
    inputs=gr.Audio(type="filepath"),
    outputs="text",
    title="Whisper Large v2 Uzbek STT",
    theme="default",
    description="Realtime demo for Uzbek speech recognition using a fine-tuned Whisper small model.",
)

iface.launch(share=True)

Device set to use cuda:0


* Running on local URL:  http://127.0.0.1:7861
* Running on public URL: https://2eda7f6dcb887c8de4.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


In [ ]:
from transformers import AutoProcessor, AutoModelForSpeechSeq2Seq
from peft import LoraConfig, get_peft_model, TaskType # Import necessary components
from transformers import pipeline

# Load the processor and model
processor = AutoProcessor.from_pretrained("ibodullo2205/uzbek-stt")
model = AutoModelForSpeechSeq2Seq.from_pretrained("ibodullo2205/uzbek-stt")

# Define LoRA configuration
peft_config = LoraConfig(
    r=8, # Rank of the LoRA update matrices
    lora_alpha=32, # Scaling factor for the LoRA update matrices
    target_modules=["q_proj", "v_proj"], # Specify the target modules for LoRA
    lora_dropout=0.05, # Dropout probability for the LoRA layers
    bias="none", # Bias type for the LoRA layers
    task_type="SEQ_2_SEQ_LM",
)

model = get_peft_model(model, peft_config) # Apply LoRA to the model

# Initialize the pipeline
pipe = pipeline(
    task="automatic-speech-recognition", 
    model=model, 
    tokenizer=processor.tokenizer, 
    feature_extractor=processor.feature_extractor, 
    return_timestamps=True 
)

def transcribe(audio_path):
    text = pipe(audio_path)["text"]
    return text

# Example usage
audio_path = "Bu-yil-texnikumni-bitirganlar-suhbat-asosida-2-kursga-qabul-.wav"  
transcribed_text = transcribe(audio_path)
print("Transcribed Text:", transcribed_text)